In [1]:
from PyQt5.QtWidgets import QApplication, QMainWindow, QLabel, QComboBox, QPushButton, QFileDialog, QWidget, QVBoxLayout, QHBoxLayout, QSpacerItem, QSizePolicy, QFrame, QDesktopWidget, QScrollArea
from PyQt5.QtCore import Qt, QRect, QPoint, QTimer, QFileInfo
from PyQt5.QtGui import QPainter, QPen, QImage, QPixmap, QFont
import cv2
import sys
import os
import numpy as np
from PIL import Image

In [2]:
def pil_imagem_qpixmap(image):
    """Converte uma imagem PIL para QPixmap"""
    image = image.convert("RGBA")
    date = image.tobytes("raw", "RGBA")
    qimage = QImage(date, image.width, image.height, QImage.Format_RGBA8888)
    pixmap = QPixmap.fromImage(qimage)
    return pixmap

In [3]:
def zoom(img, yi, yf, xi, xf):
    z = img[yi:yf, xi:xf]
    return z

class JanelaSecundaria(QMainWindow):
    def __init__(self, file_path, x, y, tipo_arquivo, janela_principal):
        super().__init__()
        self.setWindowTitle("Manipulação de Imagens e Vídeos")
        self.setGeometry(100, 100, 1000, 800)
        self.tipo_arquivo = tipo_arquivo
        self.video_capture = None
        self.timer = QTimer()
        self.janela_principal = janela_principal
        self.original_image = None 
        self.cropped_image = None
        self.zoom_level = 1.0  
        self.rect_inicio_ponto = None 
        self.rect_fim_ponto = None
        self.roi_coords = []
        self.imagem_convolucao = None  # Armazena a imagem filtrada
        self.imagem_bin_cinza_cores = None
        self.imagem_antes_filtro = None
        self.velocidade_reproducao = 1.0  # Velocidade padrão
        self.pontos_de_corte = []  # Lista de pontos de corte
        self.operacao_cascata = False  # Operações em cascata desativadas por padrão
        self.frame_index = 0
        self.frames = []
        self.cont = 1 
        self.i = 0 
        self.f = 0 
        self.op = ""
        self.timer = QTimer()

        self._setup_ui(file_path, x, y)
        self.showMaximized()

    def _setup_ui(self, file_path, x, y):
        main_layout = QVBoxLayout()
        control_layout = QHBoxLayout()
        control_layout.setAlignment(Qt.AlignTop)
        self.image_label = QLabel(self)
        self.image_label.setAlignment(Qt.AlignCenter)

        # Seção "Aplicar Filtro"
        filtro_layout = QVBoxLayout()
        filtro_label = QLabel("Aplicar Filtro de Convolução", self)
        filtro_label.setFont(QFont("Arial", 12))
        filtro_layout.addWidget(filtro_label)
        self.filtro_combo = QComboBox(self)
        self.filtro_combo.addItems(["blur", "sharpen", "emboss", "laplacian", "canny", "sobel"])
        filtro_layout.addWidget(self.filtro_combo)
        control_layout.addLayout(filtro_layout)

        # Seção "Geração de Imagens"
        geracao_layout = QVBoxLayout()
        geracao_label = QLabel("Aplicar Fitro Cinza/Binário/Cores", self)
        geracao_label.setFont(QFont("Arial", 12))
        geracao_layout.addWidget(geracao_label)
        self.geracao_combo = QComboBox(self)
        self.geracao_combo.addItems(["cinza", "binario", "cores"])
        geracao_layout.addWidget(self.geracao_combo)
        control_layout.addLayout(geracao_layout)
        self.geracao_combo.currentIndexChanged.connect(self.aplicar_filtro_geracao)

        # Seção "Vídeo"
        self.video_layout = QVBoxLayout()
        self.video_label = QLabel("Vídeo", self)
        self.video_label.setFont(QFont("Arial", 12))
        self.video_layout.addWidget(self.video_label)

        btn_layout = QHBoxLayout()
        self.btn_voltar = QPushButton("Voltar", self)
        self.btn_avancar = QPushButton("Avançar", self)
        self.btn_inverter = QPushButton("Inverter", self)
        self.btn_pausar = QPushButton("Pausar", self)
        self.btn_desacelerar = QPushButton("Desacelerar", self)
        self.btn_acelerar = QPushButton("Acelerar", self)
        
    
        btn_layout.addWidget(self.btn_voltar)
        btn_layout.addWidget(self.btn_avancar)
        btn_layout.addWidget(self.btn_inverter)
        btn_layout.addWidget(self.btn_pausar)
        btn_layout.addWidget(self.btn_desacelerar)
        btn_layout.addWidget(self.btn_acelerar)
        
        self.video_layout.addLayout(btn_layout)

        self.video_duracao = QLabel("00:00 / 00:00", self)
        self.video_layout.addWidget(self.video_duracao)
        control_layout.addLayout(self.video_layout)

        # Área de visualização
        self.image_label = QLabel(self)
        self.scroll_area = QScrollArea(self)
        self.scroll_area.setFixedSize(700, 500)
        self.image_label.setAlignment(Qt.AlignCenter)
        self.scroll_area.setWidgetResizable(True)
        self.scroll_area.setWidget(self.image_label)

        # Remover barras de rolagem para vídeos
        if self.tipo_arquivo == "Vídeo":
            self.scroll_area.setVerticalScrollBarPolicy(Qt.ScrollBarAlwaysOff)
            self.scroll_area.setHorizontalScrollBarPolicy(Qt.ScrollBarAlwaysOff)
            self.scroll_area.setAlignment(Qt.AlignCenter)
        else:
            self.video_label.setVisible(False)
            self.btn_voltar.setVisible(False)
            self.btn_avancar.setVisible(False)
            self.btn_inverter.setVisible(False)
            self.btn_pausar.setVisible(False)
            self.btn_desacelerar.setVisible(False)
            self.btn_acelerar.setVisible(False)
            self.video_duracao.setVisible(False)
    
        # Layout de centralização
        center_layout = QVBoxLayout()
        center_layout.addStretch(1)
        center_layout.addWidget(self.scroll_area, alignment=Qt.AlignCenter)
        center_layout.addStretch(1)

        main_layout.addLayout(control_layout)
        main_layout.addLayout(center_layout)

        print(f"Carregando imagem do caminho: {file_path}")
        if self.tipo_arquivo == "Imagem":
            self.original_image = cv2.imread(file_path)
            if self.original_image is not None: 
                print("Imagem carregada com sucesso.") 
                self.carregar_imagem()
            else: 
                print("Falha ao carregar a imagem.")
        
        elif self.tipo_arquivo == "Vídeo":
            self.video_capture = cv2.VideoCapture(file_path)
            self.timer.timeout.connect(self.atualizar_quadro)
            self.timer.start(30) 

        central_widget = QWidget()
        central_widget.setLayout(main_layout)
        self.setCentralWidget(central_widget)
        self.setStyleSheet("background-color: #e6f2ff;")
    
        self._config_botoes(main_layout)

    def opencv_imagem_qpixmap(self, image):
        altura, largura, canal = image.shape
        bytes_por_linha = canal * largura
        qimage = QImage(image.data, largura, altura, bytes_por_linha, QImage.Format_RGB888)
        pixmap = QPixmap.fromImage(qimage)
        return pixmap

    def carregar_imagem(self):
        if self.original_image is not None:
            imagem = cv2.cvtColor(self.original_image, cv2.COLOR_BGR2RGB)
            pixmap = self.opencv_imagem_qpixmap(imagem)
            self.image_label.setPixmap(pixmap.scaled(1000, 500, Qt.KeepAspectRatio, Qt.SmoothTransformation))
            self.image_label.resize(1000, 500)

    def concluir_selecao(self):
        if self.selecionando:
            self.selecionando = False
            x1, y1 = min(self.start_x, self.end_x), min(self.start_y, self.end_y)
            x2, y2 = max(self.start_x, self.end_x), max(self.start_y, self.end_y)
        
            # Adicionando logs para depuração
            print(f"Initial selection coordinates: x1={x1}, y1={y1}, x2={x2}, y2={y2}")
        
            # Ajustar as coordenadas considerando a proporção de zoom
            proporcao_x = self.original_image.shape[1] / self.image_label.pixmap().width()
            proporcao_y = self.original_image.shape[0] / self.image_label.pixmap().height()
        
            x1 = int(x1 * proporcao_x)
            y1 = int(y1 * proporcao_y)
            x2 = int(x2 * proporcao_x)
            y2 = int(y2 * proporcao_y)
        
            # Adicionando logs para depuração
            print(f"Scaled selection coordinates: x1={x1}, y1={y1}, x2={x2}, y2={y2}")
        
            if self.original_image is not None:
                self.cropped_image = self.original_image[y1:y2, x1:x2]
                self.exibir_imagem(self.cropped_image)
                print("Seleção concluída e imagem recortada armazenada.")
            else:
                self.cropped_image = None
                print("Erro ao concluir a seleção: imagem original não encontrada.")

    # Função exibir_imagem atualizada para usar a imagem original
    def exibir_imagem(self, image):
        rgb_image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        pixmap = self.opencv_imagem_qpixmap(rgb_image)
        self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
        self.image_label.resize(self.scroll_area.size())
        self.scroll_area.setWidget(self.image_label)
        self.scroll_area.setWidgetResizable(True)

    def atualizar_quadro(self):
        ret, frame = self.video_capture.read()
        if ret:
            imagem = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            altura, largura, canal = imagem.shape
            passo = canal * largura
            qimage = QImage(imagem.data, largura, altura, passo, QImage.Format_RGB888)
            pixmap = QPixmap.fromImage(qimage)

            self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
            self.image_label.setFixedSize(self.scroll_area.size())
            self.scroll_area.setWidget(self.image_label)
        else:
            self.timer.stop()
            self.video_capture.release()

    def closeEvent(self, event):
        if self.video_capture is not None:
            self.video_capture.release()
        super().closeEvent(event)

    def voltar(self):
        self.close()
        self.janela_principal.show()

    def _config_botoes(self, layout):
        btn_layout = QHBoxLayout()
        btn_estilo = {
            "font-family": "Arial",
            "font-size": "15px",
            "color": "#000000",
            "background-color": "#007acc",
            "padding": "5px 20px",
            "margin": "5px",
            "width": "10px",
            "height": "10px"
        }

        self.btn_voltar_inf = self._criar_btn("Voltar", btn_estilo, self.voltar)
        self.btn_zoom_mais = self._criar_btn("Zoom+", btn_estilo, self.zoom_mais)
        self.btn_zoom_menos = self._criar_btn("Zoom-", btn_estilo, self.zoom_menos)
        self.btn_aplicar_filtro = self._criar_btn("Aplicar Filtro", btn_estilo, self.aplicar_filtro_convolucao)
        self.btn_desfaz_selecao = self._criar_btn("Desfazer Seleção", btn_estilo, self.desfazer_selecao)
        self.btn_salvar = self._criar_btn("Salvar", btn_estilo, self.salvar_recorte)
        self.btn_sair = self._criar_btn("Sair", btn_estilo, self.close)

        btn_layout.addWidget(self.btn_voltar_inf)
        btn_layout.addWidget(self.btn_zoom_mais)
        btn_layout.addWidget(self.btn_zoom_menos)
        btn_layout.addWidget(self.btn_aplicar_filtro)
        btn_layout.addWidget(self.btn_desfaz_selecao)
        btn_layout.addWidget(self.btn_salvar)
        btn_layout.addWidget(self.btn_sair)

        layout.addLayout(btn_layout)

    # Função para desfazer a seleção, zoom e filtros
    def desfazer_selecao(self):
        if self.original_image is not None:
            print("Desfazendo seleção, zoom e filtros, retornando à imagem original.")
            self.cropped_image = None
            self.rect_inicio_ponto = None
            self.rect_fim_ponto = None
            self.zoom_level = 1.0
            self.imagem_convolucao = None
            self.imagem_bin_cinza_cores = None
            self.original_image = self.imagem_antes_filtro  # Restaurar a imagem original antes do filtro
            self.aplicar_tamanho_original()  # Reseta o zoom e exibe a imagem original
            self.exibir_imagem(self.original_image)
        else:
            print("Nenhuma imagem carregada para desfazer a seleção.")


    def aplicar_filtro_geracao(self):
        if self.original_image is not None:
            filtro_selecionado = self.geracao_combo.currentText()
            print("Aplicando filtro de geração de imagem:", filtro_selecionado)
            self.imagem_bin_cinza_cores = self.aplicar_filtro_bin_cinz_cores(self.original_image, filtro_selecionado)
            self.exibir_imagem(self.imagem_bin_cinza_cores)
            # Atualizar a imagem original para a imagem filtrada
            self.original_image = self.imagem_bin_cinza_cores.copy()
        else:
            print("Nenhuma imagem carregada para aplicar o filtro de geração.")

    def aplicar_filtro_bin_cinz_cores(self, image, filter_type):
        print("Entrando na função aplicar_filtro_bin_cinz_cores")
        cv_image = np.array(image)
        if filter_type == "binario":
            _, filtered_image = cv2.threshold(cv_image, 127, 255, cv2.THRESH_BINARY)
        elif filter_type == "cinza":
            filtered_image = cv2.cvtColor(cv_image, cv2.COLOR_BGR2GRAY)
        elif filter_type == "cores":
            filtered_image = cv2.cvtColor(cv_image, cv2.COLOR_BGR2HSV)
        else:
            filtered_image = cv_image
        print(f"Filtro {filter_type} aplicado.")
        return filtered_image


    def _config_filtro(self):
        # Adicionar um método para configurar os filtros de convolução
        self.btn_filtro.clicked.connect(self.aplicar_filtro_convolucao)

    # Modificar a função aplicar_filtro_convolucao para armazenar a imagem original antes de aplicar o filtro
    def aplicar_filtro_convolucao(self):
        if self.original_image is not None:
            filtro_selecionado = self.filtro_combo.currentText()
            try:
                # Armazenar a imagem original antes de aplicar o filtro
                self.imagem_antes_filtro = self.original_image.copy()
            
                filtered_image = self.aplicar_filtro(self.original_image, filtro_selecionado)
                filtered_image_cv = np.array(filtered_image)

                if filtro_selecionado in ["laplacian", "sobel", "scharr", "prewitt"]:
                    filtered_image_cv = cv2.normalize(filtered_image_cv, None, 0, 255, cv2.NORM_MINMAX, dtype=cv2.CV_8U)

                self.exibir_imagem(filtered_image_cv)
                self.original_image = filtered_image_cv
                self.imagem_convolucao = filtered_image_cv

                print(f"Filtro {filtro_selecionado} aplicado com sucesso.")
            except Exception as e:
                print(f"Erro ao aplicar filtro: {e}")
        else:
            print("Nenhuma imagem carregada para aplicar filtro.")

    def aplicar_filtro(self, image, filter_type):
        cv_image = np.array(image)
    
        if filter_type == "blur":
            print("Aplicando filtro: blur")
            filtered_image = cv2.GaussianBlur(cv_image, (15, 15), 0)
        elif filter_type == "sharpen":
            print("Aplicando filtro: sharpen")
            kernel = np.array([[0, -1, 0], [-1, 5, -1], [0, -1, 0]])
            filtered_image = cv2.filter2D(cv_image, -1, kernel)
        elif filter_type == "emboss":
            print("Aplicando filtro: emboss")
            kernel = np.array([[0, -1, -1], [1, 0, -1], [1, 1, 0]])
            filtered_image = cv2.filter2D(cv_image, -1, kernel)
        elif filter_type == "laplacian":
            print("Aplicando filtro: laplacian")
            filtered_image = cv2.Laplacian(cv_image, cv2.CV_64F)
        elif filter_type == "canny":
            print("Aplicando filtro: canny")
            filtered_image = cv2.Canny(cv_image, 100, 200)
        elif filter_type == "sobel":
            print("Aplicando filtro: sobel")
            filtered_image = cv2.Sobel(cv_image, cv2.CV_64F, 1, 0, ksize=5)
        elif filter_type == "median_blur":
            print("Aplicando filtro: median_blur")
            filtered_image = cv2.medianBlur(cv_image, 5)
        elif filter_type == "bilateral_filter":
            print("Aplicando filtro: bilateral_filter")
            filtered_image = cv2.bilateralFilter(cv_image, 9, 75, 75)
        elif filter_type == "scharr":
            print("Aplicando filtro: scharr")
            filtered_image = cv2.Scharr(cv_image, cv2.CV_64F, 1, 0)
        elif filter_type == "prewitt":
            print("Aplicando filtro: prewitt")
            kernelx = np.array([[1, 0, -1], [1, 0, -1], [1, 0, -1]])
            kernely = np.array([[1, 1, 1], [0, 0, 0], [-1, -1, -1]])
            filtered_image_x = cv2.filter2D(cv_image, -1, kernelx)
            filtered_image_y = cv2.filter2D(cv_image, -1, kernely)
            filtered_image = cv2.addWeighted(filtered_image_x, 0.5, filtered_image_y, 0.5, 0)
        else:
            filtered_image = cv_image

        print(f"Filtro {filter_type} aplicado.")
        return filtered_image

    def _criar_btn(self, texto, estilo, chamada_retorno=None):
        btn = QPushButton(texto, self)
        btn.setStyleSheet(f"""
            font-family: {estilo['font-family']};
            font-size: {estilo['font-size']};
            color: {estilo['color']};
            background-color: {estilo['background-color']};
            padding:{estilo['padding']};
            margin: {estilo['margin']};
            width: {estilo['width']};
            height: {estilo['height']};
        """)
        btn.setFont(QFont(estilo['font-family'], int(estilo['font-size'].replace('px', ''))))
        if chamada_retorno:
            btn.clicked.connect(chamada_retorno)
        return btn

    def zoom_mais(self):
        if self.original_image is not None:
            print(f"Zoom+: Level Before: {self.zoom_level}")
            self.zoom_level = min(self.zoom_level * 1.2, 4.0)  # Mantemos um fator de 1.2 para aumento
            self.aplicar_zoom_customizado()
    
    def zoom_menos(self):
        if self.original_image is not None:
            print(f"Zoom-: Level Before: {self.zoom_level}")
            self.zoom_level = max(self.zoom_level / 1.2, 1.0)  # Mesmo fator de 1.2 para diminuição
            if self.zoom_level <= 1.01:  # Pequena margem para garantir que volte ao original
                self.zoom_level = 1.0
                self.aplicar_tamanho_original()
            else:
                self.aplicar_zoom_customizado()

    def aplicar_tamanho_original(self):
        if self.original_image is not None:
            try:
                original_img_rgb = cv2.cvtColor(self.original_image, cv2.COLOR_BGR2RGB)
                pixmap = self.opencv_imagem_qpixmap(original_img_rgb)
                self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
                self.image_label.resize(self.scroll_area.size())
                self.scroll_area.setWidget(self.image_label)
                self.scroll_area.setWidgetResizable(True)
                print("Imagem redefinida para o tamanho original.")
            except Exception as e:
                print(f"Erro ao redefinir para o tamanho original: {e}")
        else:
            print("Nenhuma imagem carregada para redefinir.") 

    def aplicar_zoom_customizado(self):
        if self.original_image is not None:
            try:
                altura, largura, _ = self.original_image.shape
                nova_altura = int(altura * self.zoom_level)
                nova_largura = int(largura * self.zoom_level)
                zoomed_img = cv2.resize(self.original_image, (nova_largura, nova_altura), interpolation=cv2.INTER_LINEAR)
                zoomed_img_rgb = cv2.cvtColor(zoomed_img, cv2.COLOR_BGR2RGB)
                pixmap = self.opencv_imagem_qpixmap(zoomed_img_rgb)
                self.image_label.setPixmap(pixmap)
                self.image_label.resize(nova_largura, nova_altura)
                self.scroll_area.setWidget(self.image_label)
                self.scroll_area.setWidgetResizable(True)
                self.scroll_area.setFixedSize(1000, 500)
                print(f"Zoom aplicado: {nova_largura}x{nova_altura}")
            except Exception as e:
                print(f"Erro ao aplicar zoom: {e}")
        else:
            print("Nenhuma imagem carregada para aplicar zoom")

    def mousePressEvent(self, event):
        if event.button() == Qt.LeftButton:
            self.rect_inicio_ponto = event.pos()
            self.rect_fim_ponto = None

    def mouseMoveEvent(self, event):
        if self.rect_inicio_ponto:
            self.rect_fim_ponto = event.pos()
            self.update()

    def mouse_release_event(self, event):
        if event.button() == Qt.LeftButton:
            if self.selecionando:
                self.end_x = event.pos().x()
                self.end_y = event.pos().y()
                print(f"Mouse released at: {self.end_x}, {self.end_y}")  # Log para depuração
                self.atualizar_selecao()
                self.concluir_selecao()  # Certifique-se de concluir a seleção

    def atualizar_selecao(self):
        if self.original_image is not None and self.selecionando:
            temp_image = self.original_image.copy()
            x1, y1 = self.start_x, self.start_y
            x2, y2 = self.end_x, self.end_y
            # Certifique-se de que as coordenadas estejam dentro dos limites
            x1, x2 = max(0, x1), min(temp_image.shape[1], x2)
            y1, y2 = max(0, y1), min(temp_image.shape[0], y2)
            # Desenhar o retângulo vermelho
            cv2.rectangle(temp_image, (x1, y1), (x2, y2), (0, 0, 255), 2)
            self.exibir_imagem(temp_image)
            print(f"Drawing rectangle from ({x1}, {y1}) to ({x2}, {y2})")  # Log para depuração
        else:
            print("Erro: Coordenadas inválidas ou imagem não carregada.")

    def salvar_recorte(self):
        if self.rect_inicio_ponto and self.rect_fim_ponto:
            # Posição do scroll
            scroll_x = self.scroll_area.horizontalScrollBar().value()
            scroll_y = self.scroll_area.verticalScrollBar().value()

            # Coordenadas de seleção ajustadas pela posição do scroll
            x1, y1 = self.rect_inicio_ponto.x() + scroll_x, self.rect_inicio_ponto.y() + scroll_y
            x2, y2 = self.rect_fim_ponto.x() + scroll_x, self.rect_fim_ponto.y() + scroll_y

            x1, x2 = sorted([x1, x2])
            y1, y2 = sorted([y1, y2])

            print(f"Before scaling: x1={x1}, y1={y1}, x2={x2}, y2={y2}")  # Log para depuração

            # Proporção de escala da imagem original em relação ao tamanho da image_label
            proporcao_x = self.original_image.shape[1] / self.image_label.pixmap().width()
            proporcao_y = self.original_image.shape[0] / self.image_label.pixmap().height()

            x1 = int(x1 * proporcao_x)
            y1 = int(y1 * proporcao_y)
            x2 = int(x2 * proporcao_x)
            y2 = int(y2 * proporcao_y)

            print(f"After scaling: x1={x1}, y1={y1}, x2={x2}, y2={y2}")  # Log para depuração

            # Aplicar o recorte na imagem atual (que pode ser a imagem filtrada e ampliada)
            recorte = self.original_image[y1:y2, x1:x2]

            # Salvar a imagem recortada e com qualquer filtro aplicado
            path_salvar = QFileDialog.getExistingDirectory(self, "C:/Users/SeuUsuario/Desktop")
            if path_salvar:
                file_path = f"{path_salvar}/imagem_recortada.jpg"
                cv2.imwrite(file_path, recorte)
                print(f"Imagem recortada salva em: {file_path}")

            self.rect_inicio_ponto = None
            self.rect_fim_ponto = None
            self.update()
        else:
            print("Nenhuma área recortada para salvar.") 

    def paintEvent(self, event):
        super().paintEvent(event)
        if self.rect_inicio_ponto and self.rect_fim_ponto:
            painter = QPainter(self)
            painter.setPen(QPen(Qt.red, 2, Qt.SolidLine))
            rect = QRect(self.rect_inicio_ponto, self.rect_fim_ponto)
            painter.drawRect(rect.normalized())

In [4]:
class JanelaSecundaria(QMainWindow):
    def __init__(self, file_path, x, y, tipo_arquivo, janela_principal):
        super().__init__()
        self.setWindowTitle("Manipulação de Imagens e Vídeos")
        self.setGeometry(100, 100, 1000, 800)
        self.file_path = file_path
        self.tipo_arquivo = tipo_arquivo
        self.video_capture = None
        self.timer = QTimer()
        self.janela_principal = janela_principal
        self.original_image = None 
        self.cropped_image = None
        self.zoom_level = 1.0  
        self.rect_inicio_ponto = None 
        self.rect_fim_ponto = None
        self.roi_coords = []
        self.imagem_convolucao = None  # Armazena a imagem filtrada
        self.imagem_bin_cinza_cores = None
        self.imagem_antes_filtro = None
        self.velocidade_reproducao = 1.0  # Velocidade padrão
        self.invertido = False
        self.pontos_de_corte = []  # Lista de pontos de corte
        self.operacao_cascata = False  # Operações em cascata desativadas por padrão
        self.frame_index = 0
        self.frames = []
        self.cont = 1 
        self.i = 0 
        self.f = 0 
        self.op = ""
        self.timer = QTimer()
        self.aplicar_filtro_video = False # Variável de controle para aplicar o filtro durante a reprodução do vídeo
        self._setup_ui(file_path, x, y)
        self.showMaximized()

        self.timer.timeout.connect(self.atualizar_quadro) 
        self.timer.start(int(1000 / (self.velocidade_reproducao * 30)))

    def _setup_ui(self, file_path, x, y):
        main_layout = QVBoxLayout()
        control_layout = QHBoxLayout()
        control_layout.setAlignment(Qt.AlignTop)
        self.image_label = QLabel(self)
        self.image_label.setAlignment(Qt.AlignCenter)

        # Seção "Aplicar Filtro"
        filtro_layout = QVBoxLayout()
        filtro_label = QLabel("Aplicar Filtro de Convolução", self)
        filtro_label.setFont(QFont("Arial", 12))
        filtro_layout.addWidget(filtro_label)
        self.filtro_combo = QComboBox(self)
        self.filtro_combo.addItems(["blur", "sharpen", "emboss", "laplacian", "canny", "sobel"])
        filtro_layout.addWidget(self.filtro_combo)
        control_layout.addLayout(filtro_layout)

        # Conectar a mudança de filtro à função de atualização 
        self.filtro_combo.currentIndexChanged.connect(self.alterar_filtro_video)
        #self.filtro_combo.currentIndexChanged.connect(self.verificar_e_aplicar_filtro)

        # Seção "Geração de Imagens"
        geracao_layout = QVBoxLayout()
        geracao_label = QLabel("Aplicar Fitro Cinza/Binário/Cores", self)
        geracao_label.setFont(QFont("Arial", 12))
        geracao_layout.addWidget(geracao_label)
        self.geracao_combo = QComboBox(self)
        self.geracao_combo.addItems(["cinza", "binario", "cores"])
        geracao_layout.addWidget(self.geracao_combo)
        control_layout.addLayout(geracao_layout)
        self.geracao_combo.currentIndexChanged.connect(self.aplicar_filtro_geracao)
        #self.geracao_combo.currentIndexChanged.connect(self.aplicar_filtro_geracao_video)
    

        # Seção "Vídeo"
        self.video_layout = QVBoxLayout()
        self.video_label = QLabel("Vídeo", self)
        self.video_label.setFont(QFont("Arial", 12))
        self.video_layout.addWidget(self.video_label)

        btn_layout = QHBoxLayout()
        #self.btn_voltar = QPushButton("Voltar", self)
        self.btn_webcam = QPushButton("Abrir webcam", self)
        #self.btn_webcam.clicked.connect(self.abrir_webcam)
        self.btn_inverter = QPushButton("Inverter", self)
        self.btn_inverter.clicked.connect(self.inverter)
        self.btn_pausar = QPushButton("Pausar", self)
        self.btn_pausar.clicked.connect(self.pausar)
        self.btn_parar = QPushButton("Parar", self)
        self.btn_parar.clicked.connect(self.parar) 
        self.btn_acelerar = QPushButton("Acelerar/Desacelerar", self)
       # self.btn_acelerar = QPushButton("Acelerar", self)
        self.btn_vel_025 = QPushButton("0.25x", self)  # Botão para velocidade 0.25x
        self.btn_vel_025.clicked.connect(lambda: self.set_velocidade_reproducao(0.25))
        self.btn_vel_1 = QPushButton("1x", self)  # Botão para velocidade 1x
        self.btn_vel_1.clicked.connect(lambda: self.set_velocidade_reproducao(1.0))
        self.btn_vel_2 = QPushButton("2x", self)  # Botão para velocidade 2x
        self.btn_vel_2.clicked.connect(lambda: self.set_velocidade_reproducao(2.0))
        
    
        #btn_layout.addWidget(self.btn_voltar)
        btn_layout.addWidget(self.btn_webcam)
        btn_layout.addWidget(self.btn_inverter)
        btn_layout.addWidget(self.btn_pausar)
        btn_layout.addWidget(self.btn_parar)
        #btn_layout.addWidget(self.btn_desacelerar)
        btn_layout.addWidget(self.btn_acelerar)
        btn_layout.addWidget(self.btn_vel_025)
        btn_layout.addWidget(self.btn_vel_1)
        btn_layout.addWidget(self.btn_vel_2)
        
        self.video_layout.addLayout(btn_layout)

        self.video_duracao = QLabel("00:00 / 00:00", self)
        self.video_layout.addWidget(self.video_duracao)
        control_layout.addLayout(self.video_layout)

        # Área de visualização
        self.image_label = QLabel(self)
        self.scroll_area = QScrollArea(self)
        self.scroll_area.setFixedSize(700, 500)
        self.image_label.setAlignment(Qt.AlignCenter)
        self.scroll_area.setWidgetResizable(True)
        self.scroll_area.setWidget(self.image_label)

        # Remover barras de rolagem para vídeos
        if self.tipo_arquivo == "Vídeo":
            self.scroll_area.setVerticalScrollBarPolicy(Qt.ScrollBarAlwaysOff)
            self.scroll_area.setHorizontalScrollBarPolicy(Qt.ScrollBarAlwaysOff)
            self.scroll_area.setAlignment(Qt.AlignCenter)
        else:
            self.video_label.setVisible(False)
            #self.btn_voltar.setVisible(False)
            self.btn_webcam.setVisible(False)
            self.btn_inverter.setVisible(False)
            self.btn_pausar.setVisible(False)
            self.btn_parar.setVisible(False)
            #self.btn_desacelerar.setVisible(False)
            self.btn_acelerar.setVisible(False)
            self.video_duracao.setVisible(False)
            self.btn_vel_025.setVisible(False)
            self.btn_vel_1.setVisible(False)
            self.btn_vel_2.setVisible(False)
    
        # Layout de centralização
        center_layout = QVBoxLayout()
        center_layout.addStretch(1)
        center_layout.addWidget(self.scroll_area, alignment=Qt.AlignCenter)
        center_layout.addStretch(1)

        main_layout.addLayout(control_layout)
        main_layout.addLayout(center_layout)

        print(f"Carregando imagem do caminho: {file_path}")
        if self.tipo_arquivo == "Imagem":
            self.original_image = cv2.imread(file_path)
            if self.original_image is not None: 
                print("Imagem carregada com sucesso.") 
                self.carregar_imagem()
            else: 
                print("Falha ao carregar a imagem.")
        
        elif self.tipo_arquivo == "Vídeo":
            self.video_capture = cv2.VideoCapture(file_path)
            self.timer.timeout.connect(self.atualizar_quadro)
            self.timer.start(30) 

        elif self.tipo_arquivo == "Vídeo":
            self.video_capture = cv2.VideoCapture(file_path)
            if not self.video_capture.isOpened():
                print("Erro ao abrir o vídeo.")
                self.video_capture = None
            else:
                self.timer.timeout.connect(self.atualizar_quadro)
                #self.timer.start(30) 
                self.processar_video() # Chama a função processar_video ao carregar o vídeo

        central_widget = QWidget()
        central_widget.setLayout(main_layout)
        self.setCentralWidget(central_widget)
        self.setStyleSheet("background-color: #e6f2ff;")
    
        self._config_botoes(main_layout)

    def opencv_imagem_qpixmap(self, image):
        altura, largura, canal = image.shape
        bytes_por_linha = canal * largura
        qimage = QImage(image.data, largura, altura, bytes_por_linha, QImage.Format_RGB888)
        pixmap = QPixmap.fromImage(qimage)
        return pixmap

    def carregar_imagem(self):
        if self.original_image is not None:
            imagem = cv2.cvtColor(self.original_image, cv2.COLOR_BGR2RGB)
            pixmap = self.opencv_imagem_qpixmap(imagem)
            self.image_label.setPixmap(pixmap.scaled(1000, 500, Qt.KeepAspectRatio, Qt.SmoothTransformation))
            self.image_label.resize(1000, 500)

    def carregar_video_original(self):
        if self.file_path:
            self.video_capture = cv2.VideoCapture(self.file_path)  # Reabre o arquivo de vídeo original
            if not self.video_capture.isOpened():
                print("Erro ao abrir o vídeo.")
                return
            self.frame_index = 0  # Reinicia o índice do quadro
            self.timer.timeout.connect(self.atualizar_quadro)  # Conecta o timer ao método de atualização de quadros
            self.timer.start(int(1000 / (self.velocidade_reproducao * 30)))  # Inicia o timer com o intervalo baseado na velocidade de reprodução
            print("Vídeo original recarregado.")
        else:
            print("Nenhum caminho de arquivo fornecido para carregar o vídeo.")

    def abrir_webcam(self):
        self.video_capture = cv2.VideoCapture(0)  # 0 para a câmera padrão do laptop
        if not self.video_capture.isOpened():
            print("[DEBUG] Erro ao acessar a webcam.")
            return

        self.timer.timeout.connect(self.atualizar_quadro_webcam)
        self.timer.start(30)
        print("[DEBUG] Webcam iniciada com sucesso.")

    def atualizar_quadro_webcam(self):
        ret, frame = self.video_capture.read()
        if ret:
            imagem = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            altura, largura, canal = imagem.shape
            passo = canal * largura
            qimage = QImage(imagem.data, largura, altura, passo, QImage.Format_RGB888)
            pixmap = QPixmap.fromImage(qimage)

            self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
            self.image_label.setFixedSize(self.scroll_area.size())
            self.scroll_area.setWidget(self.image_label)
        else:
            print("[DEBUG] Não foi possível ler o quadro da webcam.")


    def concluir_selecao(self):
        if self.selecionando:
            self.selecionando = False
            x1, y1 = min(self.start_x, self.end_x), min(self.start_y, self.end_y)
            x2, y2 = max(self.start_x, self.end_x), max(self.start_y, self.end_y)
        
            # Adicionando logs para depuração
            print(f"Initial selection coordinates: x1={x1}, y1={y1}, x2={x2}, y2={y2}")
        
            # Ajustar as coordenadas considerando a proporção de zoom
            proporcao_x = self.original_image.shape[1] / self.image_label.pixmap().width()
            proporcao_y = self.original_image.shape[0] / self.image_label.pixmap().height()
        
            x1 = int(x1 * proporcao_x)
            y1 = int(y1 * proporcao_y)
            x2 = int(x2 * proporcao_x)
            y2 = int(y2 * proporcao_y)
        
            # Adicionando logs para depuração
            print(f"Scaled selection coordinates: x1={x1}, y1={y1}, x2={x2}, y2={y2}")
        
            if self.original_image is not None:
                self.cropped_image = self.original_image[y1:y2, x1:x2]
                self.exibir_imagem(self.cropped_image)
                print("Seleção concluída e imagem recortada armazenada.")
            else:
                self.cropped_image = None
                print("Erro ao concluir a seleção: imagem original não encontrada.")

    # Função exibir_imagem atualizada para usar a imagem original
    def exibir_imagem(self, image):
        rgb_image = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        pixmap = self.opencv_imagem_qpixmap(rgb_image)
        self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
        self.image_label.resize(self.scroll_area.size())
        self.scroll_area.setWidget(self.image_label)
        self.scroll_area.setWidgetResizable(True)

    """def processar_video(self):
        cap = self.video_capture
        while True:
            rval, frame = cap.read()
            if not rval:
                cap.set(cv2.CAP_PROP_POS_FRAMES, 0)
                continue

            if self.velocidade_reproducao == 0:
                self.velocidade_reproducao = 1

            # Aplicar filtro se selecionado
            if self.aplicar_filtro_geracao:
                frame = self.aplicar_filtro_bin_cinz_cores(frame, self.filtro_selecionado_geracao)

            # Converter a imagem para exibição
            imagem = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            altura, largura, canal = imagem.shape
            passo = canal * largura
            qimage = QImage(imagem.data, largura, altura, passo, QImage.Format_RGB888)
            pixmap = QPixmap.fromImage(qimage)
            self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
            self.image_label.setFixedSize(self.scroll_area.size())
            self.scroll_area.setWidget(self.image_label)

            key = cv2.waitKey(int(1000 / self.velocidade_reproducao)) & 0xFF
            if key == ord('q'):
                break
            elif key == ord('z'):
                self.op = "z"
            elif key == ord('n'):
                self.op = ""
            elif key == ord('p'):
                self.velocidade_reproducao = -1
                self.op = 'p'
            elif key == ord('v'):
                self.velocidade_reproducao = 10
            elif key == ord('i'):
                self.i = self.cont
            elif key == ord('f') and self.i != 0:
                self.f = self.cont
            elif key == ord('-'):
                self.velocidade_reproducao = max(self.velocidade_reproducao + 5, 1)
            elif key == ord('+'):
                self.velocidade_reproducao = max(self.velocidade_reproducao - 5, 1)
            elif key == ord('s'):
                if self.op == 'p':
                    cv2.imwrite(path_salvar+'frame_alterado.jpg', frame)
                if self.i != 0 and self.f != 0:
                    break

            print(self.cont)
            self.cont += 1
        cap.release()
        print('Finalizou a geração dos frames.')
        if self.i != 0 and self.f != 0:
            self.salvar_frames(self.i, self.f) """

    def processar_video(self):
        cap = self.video_capture
        self.cont = 0
        self.i = 0
        self.f = 0

        while True:
            rval, frame = cap.read()
            if not rval:
                cap.set(cv2.CAP_PROP_POS_FRAMES, 0)
                continue

            if self.velocidade_reproducao == 0:
                self.velocidade_reproducao = 1

            # Aplicar filtro de convolução se habilitado
            if self.aplicar_filtro_video:
                frame = self.aplicar_filtro(frame, self.filtro_selecionado_video)

            # Aplicar filtro de geração de imagem se habilitado
            if self.aplicar_filtro_geracao:
                frame = self.aplicar_filtro_bin_cinz_cores(frame, self.filtro_selecionado_geracao)

            # Converter a imagem para exibição
            imagem = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            altura, largura, canal = imagem.shape
            passo = canal * largura
            qimage = QImage(imagem.data, largura, altura, passo, QImage.Format_RGB888)
            pixmap = QPixmap.fromImage(qimage)
            self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
            self.image_label.setFixedSize(self.scroll_area.size())
            self.scroll_area.setWidget(self.image_label)

            key = cv2.waitKey(int(1000 / self.velocidade_reproducao)) & 0xFF
            if key == ord('q'):
                break
            elif key == ord('z'):
                self.op = "z"
            elif key == ord('n'):
                self.op = ""
            elif key == ord('p'):
                self.velocidade_reproducao = -1
                self.op = 'p'
            elif key == ord('v'):
                self.velocidade_reproducao = 10
            elif key == ord('i'):
                self.i = self.cont
            elif key == ord('f') and self.i != 0:
                self.f = self.cont
            elif key == ord('-'):
                self.velocidade_reproducao = max(self.velocidade_reproducao + 5, 1)
            elif key == ord('+'):
                self.velocidade_reproducao = max(self.velocidade_reproducao - 5, 1)
            elif key == ord('s'):
                if self.op == 'p':
                    cv2.imwrite('frame_alterado.jpg', frame)  # Salva o quadro atual como uma imagem
                if self.i != 0 and self.f != 0:
                    break

            print(self.cont)
            self.cont += 1

        cap.release()
        print('Finalizou a geração dos frames.')
        if self.i != 0 and self.f != 0:
            self.salvar_frames(self.i, self.f)



    def atualizar_quadro(self):
        ret, frame = self.video_capture.read()
        if ret:
            if self.aplicar_filtro_video:
                frame = self.aplicar_filtro(frame, self.filtro_selecionado_video)
            
            imagem = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            altura, largura, canal = imagem.shape
            passo = canal * largura
            qimage = QImage(imagem.data, largura, altura, passo, QImage.Format_RGB888)
            pixmap = QPixmap.fromImage(qimage)

            self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
            self.image_label.setFixedSize(self.scroll_area.size())
            self.scroll_area.setWidget(self.image_label)
        else:
            self.timer.stop()
            self.video_capture.release() 

    """def atualizar_quadro(self):
        if self.tipo_arquivo == "Vídeo" and self.video_capture is not None and self.video_capture.isOpened():
            ret, frame = self.video_capture.read()
            if ret:
                # Aplicar filtros de convolução se habilitados
                if self.aplicar_filtro_video:
                    frame = self.aplicar_filtro(frame, self.filtro_selecionado_video)

                # Aplicar filtros de geração de imagem
                filtro_selecionado = self.geracao_combo.currentText()
                frame = self.aplicar_filtro_bin_cinz_cores(frame, filtro_selecionado)
                print(f"[DEBUG] Filtro {filtro_selecionado} aplicado ao quadro de vídeo.")

                imagem = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
                altura, largura, canal = imagem.shape
                passo = canal * largura
                qimage = QImage(imagem.data, largura, altura, passo, QImage.Format_RGB888)
                pixmap = QPixmap.fromImage(qimage)

                self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
                self.image_label.setFixedSize(self.scroll_area.size())
                self.scroll_area.setWidget(self.image_label)
            else:
                print("[DEBUG] Não foi possível ler o quadro.")
                self.timer.stop()
                self.video_capture.release()
        else:
            print("[DEBUG] Erro: video_capture não foi inicializado corretamente ou não é um vídeo.") """


    def voltar(self):
        self.video_capture.set(cv2.CAP_PROP_POS_FRAMES, max(self.video_capture.get(cv2.CAP_PROP_POS_FRAMES) - 30, 0))

    def avancar(self):
        self.video_capture.set(cv2.CAP_PROP_POS_FRAMES, self.video_capture.get(cv2.CAP_PROP_POS_FRAMES) + 30)

    def inverter(self):
        self.invertido = not self.invertido
        print(f"Inversão do vídeo: {'Ativada' if self.invertido else 'Desativada'}")

        # Reiniciar o temporizador para ajustar o intervalo do quadro corretamente
        if self.invertido:
            self.timer.stop()
            self.timer.start(int(1000 / (self.velocidade_reproducao * 30)))
        else:
            self.timer.stop()
            self.timer.start(int(1000 / (self.velocidade_reproducao * 30)))

        # Inicialização do temporizador
        self.timer = QTimer()
        self.timer.timeout.connect(self.atualizar_quadro)
        self.timer.start(int(1000 / (self.velocidade_reproducao * 30)))

    def reproduzir(self):
         # Se o vídeo está invertido
         if self.invertido:
             frame_pos = self.video_capture.get(cv2.CAP_PROP_POS_FRAMES)
             if frame_pos <= 0:  # Se o vídeo está no início, rebobina para o final
                 self.video_capture.set(cv2.CAP_PROP_POS_FRAMES, self.video_capture.get(cv2.CAP_PROP_FRAME_COUNT) - 1)
             else:
                 self.video_capture.set(cv2.CAP_PROP_POS_FRAMES, frame_pos - 1)
         else:
             # Reprodução normal
             self.video_capture.set(cv2.CAP_PROP_POS_FRAMES, self.video_capture.get(cv2.CAP_PROP_POS_FRAMES) + 1)

         if not self.timer.isActive():
             self.timer.start(int(1000 / (self.velocidade_reproducao * 30)))

    def parar(self):
        if self.video_capture is not None:
            self.video_capture.release()
        self.timer.stop()
        self.image_label.clear()


    def pausar(self):
        self.timer.stop()

    def set_velocidade_reproducao(self, velocidade):
        self.velocidade_reproducao = velocidade
        self.timer.start(int(1000 / (self.velocidade_reproducao * 30)))


    def closeEvent(self, event):
        if self.video_capture is not None:
            self.video_capture.release()
        super().closeEvent(event)

    def voltar(self):
        self.close()
        self.janela_principal.show()

    def _config_botoes(self, layout):
        btn_layout = QHBoxLayout()
        btn_estilo = {
            "font-family": "Arial",
            "font-size": "15px",
            "color": "#000000",
            "background-color": "#007acc",
            "padding": "5px 20px",
            "margin": "5px",
            "width": "10px",
            "height": "10px"
        }

        self.btn_voltar_inf = self._criar_btn("Voltar", btn_estilo, self.voltar)
        self.btn_zoom_mais = self._criar_btn("Zoom+", btn_estilo, self.zoom_mais)
        self.btn_zoom_menos = self._criar_btn("Zoom-", btn_estilo, self.zoom_menos)
        self.btn_aplicar_filtro = self._criar_btn("Aplicar Filtro", btn_estilo, self.aplicar_filtro_convolucao_imagem)
        self.btn_desfaz_selecao = self._criar_btn("Desfazer Seleção", btn_estilo, self.desfazer_selecao)
        self.btn_salvar = self._criar_btn("Salvar", btn_estilo, self.salvar_recorte)
        self.btn_sair = self._criar_btn("Sair", btn_estilo, self.close)

        btn_layout.addWidget(self.btn_voltar_inf)
        btn_layout.addWidget(self.btn_zoom_mais)
        btn_layout.addWidget(self.btn_zoom_menos)
        btn_layout.addWidget(self.btn_aplicar_filtro)
        btn_layout.addWidget(self.btn_desfaz_selecao)
        btn_layout.addWidget(self.btn_salvar)
        btn_layout.addWidget(self.btn_sair)

        layout.addLayout(btn_layout)

    def desfazer_selecao_video(self):
        if self.tipo_arquivo == "Vídeo":  # Verifica se o arquivo é um vídeo
            print("Desfazendo seleção, filtros e retornando ao vídeo original.")
            self.invertido = False  # Desfaz a inversão do vídeo, se aplicada
            self.aplicar_filtro_video = False  # Desativa a aplicação de filtros
            self.filtro_selecionado_video = None  # Remove o filtro selecionado
            self.video_capture.set(cv2.CAP_PROP_POS_FRAMES, 0)  # Reinicia o vídeo ao primeiro quadro
            self.carregar_video_original()  # Carrega o vídeo original
            print("Configurações de vídeo redefinidas e vídeo original carregado.")
        else:
            print("Nenhuma ação realizada para imagens.")

    

    def desfazer_selecao(self):
        if self.tipo_arquivo == "Imagem":  # Verifica se o arquivo é uma imagem
            if self.original_image is not None:
                print("Desfazendo seleção, zoom e filtros, retornando à imagem original.")
                self.cropped_image = None
                self.rect_inicio_ponto = None
                self.rect_fim_ponto = None
                self.zoom_level = 1.0
                self.imagem_convolucao = None
                self.imagem_bin_cinza_cores = None
                self.original_image = self.imagem_antes_filtro  # Restaurar a imagem original antes do filtro
                self.aplicar_tamanho_original()  # Reseta o zoom e exibe a imagem original
                self.exibir_imagem(self.original_image)
            else:
                print("Nenhuma imagem carregada para desfazer a seleção.")
        elif self.tipo_arquivo == "Vídeo":
            self.desfazer_selecao_video()  # Chama a função específica para desfazer seleção no vídeo


    """def aplicar_filtro_geracao(self):
        if self.original_image is not None:
            filtro_selecionado = self.geracao_combo.currentText()
            print("Aplicando filtro de geração de imagem:", filtro_selecionado)
            self.imagem_bin_cinza_cores = self.aplicar_filtro_bin_cinz_cores(self.original_image, filtro_selecionado)
            self.exibir_imagem(self.imagem_bin_cinza_cores)
            # Atualizar a imagem original para a imagem filtrada
            self.original_image = self.imagem_bin_cinza_cores.copy()
        else:
            print("Nenhuma imagem carregada para aplicar o filtro de geração.")"""


    def aplicar_filtro_geracao(self):
        if self.original_image is not None:
            filtro_selecionado = self.geracao_combo.currentText()
            print("Aplicando filtro de geração de imagem:", filtro_selecionado)
            self.imagem_bin_cinza_cores = self.aplicar_filtro_bin_cinz_cores(self.original_image, filtro_selecionado)
            self.exibir_imagem(self.imagem_bin_cinza_cores)
            # Atualizar a imagem original para a imagem filtrada
            self.original_image = self.imagem_bin_cinza_cores.copy() 
        else:
            print("Nenhuma imagem carregada para aplicar o filtro de geração.")

    def aplicar_filtro_geracao_video(self):
        if self.video_capture is not None:
            filtro_selecionado = self.geracao_combo.currentText()
            print("Aplicando filtro de geração de vídeo:", filtro_selecionado)
            self.filtro_selecionado_video = filtro_selecionado
            self.aplicar_filtro_video = True
        else:
            print("Nenhum vídeo carregado para aplicar o filtro de geração.")


    def aplicar_filtro_bin_cinz_cores(self, image, filter_type):
        print("Entrando na função aplicar_filtro_bin_cinz_cores")
        cv_image = np.array(image)
        if filter_type == "binario":
            _, filtered_image = cv2.threshold(cv_image, 127, 255, cv2.THRESH_BINARY)
            print("[DEBUG] Filtro binário aplicado.")
        elif filter_type == "cinza":
            filtered_image = cv2.cvtColor(cv_image, cv2.COLOR_BGR2GRAY)
            print("[DEBUG] Filtro cinza aplicado.")
        elif filter_type == "cores":
            filtered_image = cv2.cvtColor(cv_image, cv2.COLOR_BGR2HSV)
            print("[DEBUG] Filtro cores aplicado.")
        else:
            filtered_image = cv_image
        print(f"Filtro {filter_type} aplicado.")
        return filtered_image

    # Modificar a função aplicar_filtro_convolucao para armazenar a imagem original antes de aplicar o filtro
    def aplicar_filtro_convolucao_imagem(self):
        if self.original_image is not None:
            filtro_selecionado = self.filtro_combo.currentText()
            try:
                # Armazenar a imagem original antes de aplicar o filtro
                self.imagem_antes_filtro = self.original_image.copy()
            
                filtered_image = self.aplicar_filtro(self.original_image, filtro_selecionado)
                filtered_image_cv = np.array(filtered_image)

                if filtro_selecionado in ["laplacian", "sobel", "scharr", "prewitt"]:
                    filtered_image_cv = cv2.normalize(filtered_image_cv, None, 0, 255, cv2.NORM_MINMAX, dtype=cv2.CV_8U)

                self.exibir_imagem(filtered_image_cv)
                self.original_image = filtered_image_cv
                self.imagem_convolucao = filtered_image_cv

                print(f"Filtro {filtro_selecionado} aplicado com sucesso.")
            except Exception as e:
                print(f"Erro ao aplicar filtro: {e}")
        else:
            print("Nenhuma imagem carregada para aplicar filtro.")

    def alterar_filtro_video(self): 
        self.aplicar_filtro_video = True 
        self.filtro_selecionado_video = self.filtro_combo.currentText() 
        print(f"[DEBUG] Filtro de vídeo selecionado: {self.filtro_selecionado_video}")

    def aplicar_filtro(self, image, filter_type):
        cv_image = np.array(image)
    
        if filter_type == "blur":
            print("Aplicando filtro: blur")
            filtered_image = cv2.GaussianBlur(cv_image, (15, 15), 0)
        elif filter_type == "sharpen":
            print("Aplicando filtro: sharpen")
            kernel = np.array([[0, -1, 0], [-1, 5, -1], [0, -1, 0]])
            filtered_image = cv2.filter2D(cv_image, -1, kernel)
        elif filter_type == "emboss":
            print("Aplicando filtro: emboss")
            kernel = np.array([[0, -1, -1], [1, 0, -1], [1, 1, 0]])
            filtered_image = cv2.filter2D(cv_image, -1, kernel)
        elif filter_type == "laplacian":
            print("Aplicando filtro: laplacian")
            filtered_image = cv2.Laplacian(cv_image, cv2.CV_64F)
            filtered_image = cv2.convertScaleAbs(filtered_image) # Converte para um formato suportado
        elif filter_type == "canny":
            print("Aplicando filtro: canny")
            filtered_image = cv2.Canny(cv_image, 100, 200)
        elif filter_type == "sobel":
            print("Aplicando filtro: sobel")
            filtered_image = cv2.Sobel(cv_image, cv2.CV_64F, 1, 0, ksize=5)
            filtered_image = cv2.convertScaleAbs(filtered_image) # Converte para um formato suportado
        elif filter_type == "median_blur":
            print("Aplicando filtro: median_blur")
            filtered_image = cv2.medianBlur(cv_image, 5)
        elif filter_type == "bilateral_filter":
            print("Aplicando filtro: bilateral_filter")
            filtered_image = cv2.bilateralFilter(cv_image, 9, 75, 75)
        elif filter_type == "scharr":
            print("Aplicando filtro: scharr")
            filtered_image = cv2.Scharr(cv_image, cv2.CV_64F, 1, 0)
        elif filter_type == "prewitt":
            print("Aplicando filtro: prewitt")
            kernelx = np.array([[1, 0, -1], [1, 0, -1], [1, 0, -1]])
            kernely = np.array([[1, 1, 1], [0, 0, 0], [-1, -1, -1]])
            filtered_image_x = cv2.filter2D(cv_image, -1, kernelx)
            filtered_image_y = cv2.filter2D(cv_image, -1, kernely)
            filtered_image = cv2.addWeighted(filtered_image_x, 0.5, filtered_image_y, 0.5, 0)
        else:
            filtered_image = cv_image

        print(f"Filtro {filter_type} aplicado.")
        return filtered_image

    def _criar_btn(self, texto, estilo, chamada_retorno=None):
        btn = QPushButton(texto, self)
        btn.setStyleSheet(f"""
            font-family: {estilo['font-family']};
            font-size: {estilo['font-size']};
            color: {estilo['color']};
            background-color: {estilo['background-color']};
            padding:{estilo['padding']};
            margin: {estilo['margin']};
            width: {estilo['width']};
            height: {estilo['height']};
        """)
        btn.setFont(QFont(estilo['font-family'], int(estilo['font-size'].replace('px', ''))))
        if chamada_retorno:
            btn.clicked.connect(chamada_retorno)
        return btn

    def zoom_mais(self):
        if self.original_image is not None:
            print(f"Zoom+: Level Before: {self.zoom_level}")
            self.zoom_level = min(self.zoom_level * 1.2, 4.0)  # Mantemos um fator de 1.2 para aumento
            self.aplicar_zoom_customizado()
    
    def zoom_menos(self):
        if self.original_image is not None:
            print(f"Zoom-: Level Before: {self.zoom_level}")
            self.zoom_level = max(self.zoom_level / 1.2, 1.0)  # Mesmo fator de 1.2 para diminuição
            if self.zoom_level <= 1.01:  # Pequena margem para garantir que volte ao original
                self.zoom_level = 1.0
                self.aplicar_tamanho_original()
            else:
                self.aplicar_zoom_customizado()

    def aplicar_tamanho_original(self):
        if self.original_image is not None:
            try:
                original_img_rgb = cv2.cvtColor(self.original_image, cv2.COLOR_BGR2RGB)
                pixmap = self.opencv_imagem_qpixmap(original_img_rgb)
                self.image_label.setPixmap(pixmap.scaled(self.scroll_area.size(), Qt.KeepAspectRatio, Qt.SmoothTransformation))
                self.image_label.resize(self.scroll_area.size())
                self.scroll_area.setWidget(self.image_label)
                self.scroll_area.setWidgetResizable(True)
                print("Imagem redefinida para o tamanho original.")
            except Exception as e:
                print(f"Erro ao redefinir para o tamanho original: {e}")
        else:
            print("Nenhuma imagem carregada para redefinir.") 

    def aplicar_zoom_customizado(self):
        if self.original_image is not None:
            try:
                altura, largura, _ = self.original_image.shape
                nova_altura = int(altura * self.zoom_level)
                nova_largura = int(largura * self.zoom_level)
                zoomed_img = cv2.resize(self.original_image, (nova_largura, nova_altura), interpolation=cv2.INTER_LINEAR)
                zoomed_img_rgb = cv2.cvtColor(zoomed_img, cv2.COLOR_BGR2RGB)
                pixmap = self.opencv_imagem_qpixmap(zoomed_img_rgb)
                self.image_label.setPixmap(pixmap)
                self.image_label.resize(nova_largura, nova_altura)
                self.scroll_area.setWidget(self.image_label)
                self.scroll_area.setWidgetResizable(True)
                self.scroll_area.setFixedSize(1000, 500)
                print(f"Zoom aplicado: {nova_largura}x{nova_altura}")
            except Exception as e:
                print(f"Erro ao aplicar zoom: {e}")
        else:
            print("Nenhuma imagem carregada para aplicar zoom")

    def mousePressEvent(self, event):
        if event.button() == Qt.LeftButton:
            self.rect_inicio_ponto = event.pos()
            self.rect_fim_ponto = None

    def mouseMoveEvent(self, event):
        if self.rect_inicio_ponto:
            self.rect_fim_ponto = event.pos()
            self.update()

    def mouse_release_event(self, event):
        if event.button() == Qt.LeftButton:
            if self.selecionando:
                self.end_x = event.pos().x()
                self.end_y = event.pos().y()
                print(f"Mouse released at: {self.end_x}, {self.end_y}")  # Log para depuração
                self.atualizar_selecao()
                self.concluir_selecao()  # Certifique-se de concluir a seleção

    def atualizar_selecao(self):
        if self.original_image is not None and self.selecionando:
            temp_image = self.original_image.copy()
            x1, y1 = self.start_x, self.start_y
            x2, y2 = self.end_x, self.end_y
            # Certifique-se de que as coordenadas estejam dentro dos limites
            x1, x2 = max(0, x1), min(temp_image.shape[1], x2)
            y1, y2 = max(0, y1), min(temp_image.shape[0], y2)
            # Desenhar o retângulo vermelho
            cv2.rectangle(temp_image, (x1, y1), (x2, y2), (0, 0, 255), 2)
            self.exibir_imagem(temp_image)
            print(f"Drawing rectangle from ({x1}, {y1}) to ({x2}, {y2})")  # Log para depuração
        else:
            print("Erro: Coordenadas inválidas ou imagem não carregada.")

    def salvar_recorte(self):
        if self.rect_inicio_ponto and self.rect_fim_ponto:
            # Posição do scroll
            scroll_x = self.scroll_area.horizontalScrollBar().value()
            scroll_y = self.scroll_area.verticalScrollBar().value()

            # Coordenadas de seleção ajustadas pela posição do scroll
            x1, y1 = self.rect_inicio_ponto.x() + scroll_x, self.rect_inicio_ponto.y() + scroll_y
            x2, y2 = self.rect_fim_ponto.x() + scroll_x, self.rect_fim_ponto.y() + scroll_y

            x1, x2 = sorted([x1, x2])
            y1, y2 = sorted([y1, y2])

            print(f"Before scaling: x1={x1}, y1={y1}, x2={x2}, y2={y2}")  # Log para depuração

            # Proporção de escala da imagem original em relação ao tamanho da image_label
            proporcao_x = self.original_image.shape[1] / self.image_label.pixmap().width()
            proporcao_y = self.original_image.shape[0] / self.image_label.pixmap().height()

            x1 = int(x1 * proporcao_x)
            y1 = int(y1 * proporcao_y)
            x2 = int(x2 * proporcao_x)
            y2 = int(y2 * proporcao_y)

            print(f"After scaling: x1={x1}, y1={y1}, x2={x2}, y2={y2}")  # Log para depuração

            # Aplicar o recorte na imagem atual (que pode ser a imagem filtrada e ampliada)
            recorte = self.original_image[y1:y2, x1:x2]

            # Salvar a imagem recortada e com qualquer filtro aplicado
            path_salvar = QFileDialog.getExistingDirectory(self, "C:/Users/SeuUsuario/Desktop")
            if path_salvar:
                file_path = f"{path_salvar}/imagem_recortada.jpg"
                cv2.imwrite(file_path, recorte)
                print(f"Imagem recortada salva em: {file_path}")

            self.rect_inicio_ponto = None
            self.rect_fim_ponto = None
            self.update()
        else:
            print("Nenhuma área recortada para salvar.") 

    def paintEvent(self, event):
        super().paintEvent(event)
        if self.rect_inicio_ponto and self.rect_fim_ponto:
            painter = QPainter(self)
            painter.setPen(QPen(Qt.red, 2, Qt.SolidLine))
            rect = QRect(self.rect_inicio_ponto, self.rect_fim_ponto)
            painter.drawRect(rect.normalized())

In [5]:
def selecionar_arq(parent, modo, tipo_arquivo):
    options = QFileDialog.Options()
    options |= QFileDialog.DontUseNativeDialog
    file_dialog = QFileDialog()
    file_dialog.setDirectory(os.path.expanduser("C:Users/walla/documents/"))
    file_path, _ = file_dialog.getOpenFileName(
        parent, 
        "Selecionar Arquivo", 
        "", 
        "Todos os Arquivos (*);;Imagens (* .png * .jpg * .jpeg);;Vídeos (* .mp4 * .avi)", 
        options=options
    )
    if file_path:
        file_info = QFileInfo(file_path)
        extension = file_info.suffix().lower()
        if extension in ['png', 'jpg', 'jpeg']:
            tipo_arquivo = "Imagem"
        elif extension in ['mp4', 'avi']:
            tipo_arquivo = "Vídeo"
        else:
            print(f"Formato de arquivo não suportado: {extension}")
            return
        parent.abrir_segunda_janela(file_path, 100, 100, tipo_arquivo)  # Passar coordenadas x e y e tipo_arquivo

In [6]:
class JanelaPrincipal(QMainWindow):
    def __init__(self):
        super().__init__()
        self.setWindowTitle("Manipulação de Imagens e Vídeos")
        self.setGeometry(100, 100, 1000, 700)
        self._setup_ui() 
    
    def _setup_ui(self):  # Método correto
        self.setStyleSheet("background-color: #e6f2ff;")
        self.setFixedSize(self.size())
        self._centralizar_tela()  
        self._setup_fontes() 
        self._setup_widgets()  
        self._setup_bottoes() 

    def _setup_fontes(self): 
        self.label_fonte = QFont("Arial", 10)
        self.label_fonte.setBold(True)
        self.combo_fonte = QFont("Arial", 10)
        self.btn_fonte = QFont("Arial", 12)

    def _setup_widgets(self):
        self.tipo_arquivo_label = QLabel("Tipo de Arquivo", self)
        self.tipo_arquivo_label.setFont(self.label_fonte)
        self.tipo_arquivo_label.setStyleSheet("color: #333333; padding: 10px; background-color: #cce6ff; margin: 1px;")
        self.tipo_arquivo_label.adjustSize()
        self.tipo_arquivo_label.move(200, 150)

        self.tipo_arquivo = QComboBox(self)
        self.tipo_arquivo.addItems(["Imagem", "Vídeo"])
        self.tipo_arquivo.setFont(self.combo_fonte)
        self.tipo_arquivo.setStyleSheet("color: #333333; padding: 10px; background-color: #e6f2ff; margin: 1px;")
        self.tipo_arquivo.setMinimumContentsLength(10)
        self.tipo_arquivo.setSizeAdjustPolicy(QComboBox.AdjustToContents)
        self.tipo_arquivo.move(200, 200)

        self.modo_label = QLabel("Selecione Modo", self)
        self.modo_label.setFont(self.label_fonte)
        self.modo_label.setStyleSheet("color: #333333; padding: 10px; background-color: #cce6ff; margin: 0px;")
        self.modo_label.adjustSize()
        self.modo_label.move(670, 150)

        self.modo = QComboBox(self)
        self.modo.addItems(["Independente", "Cascata"])
        self.modo.setFont(self.combo_fonte)
        self.modo.setStyleSheet("color: #333333; padding: 10px; background-color: #e6f2ff; margin: 1px;")
        self.modo.setMinimumContentsLength(10)
        self.modo.setSizeAdjustPolicy(QComboBox.AdjustToContents)
        self.modo.move(670, 200)

    def _setup_bottoes(self):
       self.btn_avancar = QPushButton("Avançar", self)
       self.btn_avancar.setFont(self.btn_fonte)
       self.btn_avancar.setStyleSheet("background-color: #007acc; color: #ffffff;")
       self.btn_avancar.resize(self.btn_avancar.sizeHint())
       self.btn_avancar.move(200, 600)
       self.btn_avancar.clicked.connect(self.avancar)

       self.btn_sair = QPushButton("Sair", self)
       self.btn_sair.setFont(self.btn_fonte)
       self.btn_sair.setStyleSheet("background-color: red;  padding: 10px 45px;")
       self.btn_sair.resize(self.btn_sair.sizeHint())
       self.btn_sair.move(670, 600)
       self.btn_sair.clicked.connect(self.close)

    def avancar(self):
       modo = self.modo.currentText()
       tipo_arquivo = self.tipo_arquivo.currentText()
       selecionar_arq(self, modo, tipo_arquivo)

    def abrir_segunda_janela(self, file_path, x, y, tipo_arquivo):
        self.segunda_janela = JanelaSecundaria(file_path, x, y, tipo_arquivo, self)
        self.segunda_janela.showMaximized()

    def _centralizar_tela(self): 
        qt_rectangle = self.frameGeometry()
        center_point = QDesktopWidget().availableGeometry().center()
        qt_rectangle.moveCenter(center_point)
        self.move(qt_rectangle.topLeft())

In [7]:
if __name__ == "__main__":
    app = QApplication(sys.argv)
    janela_principal = JanelaPrincipal()
    janela_principal.show()
    app.exec_()

Carregando imagem do caminho: C:/Users/user/Desktop/Estudos/teti/trabalhos/manipulacao_video_img/imagens/arara-azul3.jpg
Imagem carregada com sucesso.


AttributeError: 'NoneType' object has no attribute 'read'

AttributeError: 'NoneType' object has no attribute 'read'

AttributeError: 'NoneType' object has no attribute 'read'

AttributeError: 'NoneType' object has no attribute 'read'

...

AttributeError: 'NoneType' object has no attribute 'read'

AttributeError: 'NoneType' object has no attribute 'read'

AttributeError: 'NoneType' object has no attribute 'read'

AttributeError: 'NoneType' object has no attribute 'read'

AttributeError: 'NoneType' object has no attribute 'read'